In [55]:
import pandas as pd
import numpy as np 
from tqdm import tqdm
import spotipy
from spotipy.oauth2 import SpotifyClientCredentials #To access authorised Spotify data
import pickle
import os
import pandas as pd
import numpy as np
from tqdm import tqdm

In [56]:
# Re-used code from: https://medium.com/@RareLoot/extracting-spotify-data-on-your-favourite-artist-via-python-d58bc92a4330

In [57]:
# Spotify developer page: https://developer.spotify.com/dashboard/applications/7085a21ce4124b3e89db61d750b133a7
client_id = '7085a21ce4124b3e89db61d750b133a7'
client_secret = '2b02da51f99f4470a1c2ef91f28a0957'

In [58]:
# !pip install spotipy

In [59]:
client_credentials_manager = SpotifyClientCredentials(client_id=client_id, client_secret=client_secret)
sp = spotipy.Spotify(client_credentials_manager=client_credentials_manager) #spotify object to access API #chosen artist

In [60]:
def get_artist_uri(artist_name):
    result = sp.search(artist_name) #search query
    for i in result['tracks']['items']:
        if (i['artists'][0]['name'] == artist_name):
            return i['artists'][0]['uri']
    print("Could not find uri for {}".format(artist_name))
    return None

def get_album_info_for_artist(name):
    #Extract Artist's uri
    artist_uri = get_artist_uri(name)
    #Pull all of the artist's albums
    sp_albums = sp.artist_albums(artist_uri, album_type='album')
    #Store artist's albums' names' and uris in separate lists
    album_names = []
    album_uris = []
    for i in range(len(sp_albums['items'])):
        album_names.append(sp_albums['items'][i]['name'])
        album_uris.append(sp_albums['items'][i]['uri'])

    return album_uris, album_names

def get_genres_from_artist(artist_name):
    artist_uri = get_artist_uri(artist_name)
    return sp.artist(artist_uri)['genres']

def get_album_tracks(album_uri, album_name):
    #Create keys-values of empty lists inside nested dictionary for album
    album_dict = dict()
    album_dict['album'] = [] #create empty list
    album_dict['track_number'] = []
    album_dict['id'] = []
    album_dict['song_name'] = []
    album_dict['song_uri'] = []
    tracks = sp.album_tracks(album_uri) #pull data on album tracks
    for n in range(len(tracks['items'])): #for each song track
        album_dict['album'].append(album_name) #append album name tracked via album_count
        album_dict['track_number'].append(tracks['items'][n]['track_number'])
        album_dict['id'].append(tracks['items'][n]['id'])
        album_dict['song_name'].append(tracks['items'][n]['name'])
        album_dict['song_uri'].append(tracks['items'][n]['uri'])
    return album_dict

def get_song_metadata_from_album(album_uris, album_names):
    spotify_albums = dict()
    for uri, name in zip(album_uris, album_names): 
        spotify_albums[uri] = get_album_tracks(uri, name)

    track_data = pd.DataFrame()
    for k in spotify_albums.keys():
        track_data = track_data.append(pd.DataFrame(spotify_albums[k]))
    return track_data

def build_artist_genre_data(artist_list):
    artist_genres = pd.DataFrame()
    for artist in tqdm(artist_list): 
        try:
            artist_genres = artist_genres.append(pd.DataFrame({'artist': artist, 'genres': get_genres_from_artist(artist)}))
        except Exception: 
            ""
    return artist_genres

def build_artist_song_dataset(artist_list):
    song_metadata = pd.DataFrame()
    artist_genres = pd.DataFrame()
    for artist in tqdm(artist_list):
        try:
            album_uris, album_names = get_album_info_for_artist(artist)
            curr_song_metadata = get_song_metadata_from_album(album_uris, album_names).assign(artist_name = lambda x: artist)
            song_metadata = song_metadata.append(curr_song_metadata)
            artist_genres = artist_genres.append(get_genres_from_artist(artist))
            print("Data for {} albums and genres has been collected".format(artist))
        except Exception: 
            print("Failed to collect data for {} albums and genres".format(artist))
    return song_metadata, artist_genres

def audio_features(uris):
    # Add new key-values to store audio features
    acousticness = []
    danceability = []
    energy = []
    instrumentalness = []
    liveness = []
    loudness = []
    speechiness = []
    tempo = []
    valence = []
    popularity = []
    # Create a track counter
    count = 0
    for track in tqdm(uris):
        # Pull audio features per track
        features = sp.audio_features(track)
        if features != [None]:
            # Append to relevant key-value
            acousticness.append(features[0]['acousticness'])
            danceability.append(features[0]['danceability'])
            energy.append(features[0]['energy'])
            instrumentalness.append(features[0]['instrumentalness'])
            liveness.append(features[0]['liveness'])
            loudness.append(features[0]['loudness'])
            speechiness.append(features[0]['speechiness'])
            tempo.append(features[0]['tempo'])
            valence.append(features[0]['valence'])
            # Popularity is stored elsewhere
            pop = sp.track(track)
            popularity.append(pop['popularity'])
            count = count + 1
            if count % 100 == 0: 
                pd.DataFrame({'uri': uris[:count], 
                'danceability': danceability, 
                'energy': energy, 
                'accousticness': acousticness,
                'instrumentalness': instrumentalness,
                'liveness': liveness, 
                'loudness': loudness, 
                'speechiness': speechiness, 
                'tempo': tempo, 
                'valence': valence, 
                'popularity': popularity}).to_csv("subsampled_audio_features_p3.csv")
    return pd.DataFrame({'uri': uris, 
            'danceability': danceability, 
            'energy': energy, 
            'accousticness': acousticness,
            'instrumentalness': instrumentalness,
            'liveness': liveness, 
            'loudness': loudness, 
            'speechiness': speechiness, 
            'tempo': tempo, 
            'valence': valence, 
            'popularity': popularity})

### Build music (genre + song metadata) for group of artists

In [9]:
artists = ['Kanye West', 'Chance the Rapper', 'Frank Ocean', 'Tame Impala', 'Tash Sultana', 'John Mayer', 
           'Bon Iver', 'Future', 'Drake', 'The Beatles', 'Snoh Aalegra', 'Goldlink', 
           'Anderson .Paak', 'Kendrick Lamar', 'Mura Masa', 'Alt-j']

In [24]:
artists = pd.read_csv("artists_songs.csv").artist.unique()

In [39]:
artist_genres = build_artist_genre_data(artists)



  0%|          | 0/16167 [00:00<?, ?it/s]

  0%|          | 1/16167 [00:00<3:45:23,  1.20it/s]

  0%|          | 2/16167 [00:01<2:53:41,  1.55it/s]

Could not find uri for Yung MX
Could not find uri for Yung Nation




  0%|          | 3/16167 [00:01<2:29:36,  1.80it/s]

  0%|          | 4/16167 [00:01<1:57:47,  2.29it/s]

Could not find uri for Yung Nilo




  0%|          | 5/16167 [00:02<2:24:35,  1.86it/s]

  0%|          | 6/16167 [00:02<2:13:51,  2.01it/s]

  0%|          | 7/16167 [00:02<1:50:31,  2.44it/s]

...



100%|█████████▉| 16157/16167 [1:40:26<00:03,  2.93it/s]

100%|█████████▉| 16158/16167 [1:40:26<00:03,  2.94it/s]

100%|█████████▉| 16159/16167 [1:40:26<00:02,  2.93it/s]

100%|█████████▉| 16160/16167 [1:40:27<00:02,  3.35it/s]

Could not find uri for Victor Hugo




100%|█████████▉| 16161/16167 [1:40:27<00:01,  3.29it/s]

100%|█████████▉| 16162/16167 [1:40:27<00:01,  3.19it/s]

100%|█████████▉| 16163/16167 [1:40:27<00:01,  3.62it/s]

Could not find uri for Victoria Justice




100%|█████████▉| 16164/16167 [1:40:28<00:00,  3.35it/s]

100%|█████████▉| 16165/16167 [1:40:28<00:00,  3.21it/s]

100%|█████████▉| 16166/16167 [1:40:28<00:00,  3.04it/s]

100%|██████████| 16167/16167 [1:40:29<00:00,  2.68it/s]


In [40]:
artist_genres.to_csv("all_genius_artist_genres.csv", index=False)

### Subsample Artists

In [74]:
artist_genres = pd.read_csv("all_genius_artist_genres.csv")

In [72]:
len(artist_genres.artist.unique())

10137

In [75]:
artist_genres.shape

(37004, 2)

In [80]:
list(artist_genres.genres.unique())

['icelandic hip hop',
 'icelandic pop',
 'dutch hip hop',
 'meme rap',
 'turkish hip hop',
 'emo rap',
 'melodic rap',
 'pop rap',
 'rap',
 'trap',
 'underground hip hop',
 'vapor trap',
 'atl hip hop',
 'dirty south rap',
 'southern hip hop',
 'mexican hip hop',
 'trap espanol',
 'trap mexicano',
 'dark trap',
 'miami hip hop',
 'phonk',
 'south african hip hop',
 'canadian hip hop',
 'toronto rap',
 'trap brasileiro',
 'german cloud rap',
 'gamecore',
 'jacksonville indie',
 'indonesian jazz',
 'indonesian pop',
 'grupera',
 'latin',
 'latin pop',
 'mexican pop',
 'ranchera',
 'latin arena pop',
 'doujin',
 'vocaloid',
 'rap calme',
 'chanson',
 'ye ye',
 'art pop',
 'chamber psych',
 'chillwave',
 'escape room',
 'experimental pop',
 'fluxwork',
 'hyperpop',
 'indietronica',
 'new isolationism',
 'outsider house',
 'belgian edm',
 'big room',
 'deep big room',
 'edm',
 'electro house',
 'house',
 'pop edm',
 'progressive electro house',
 'progressive house',
 'tropical house',
 'mat

In [82]:
artist_genres = artist_genres.assign(
    is_rap = lambda x: x.genres == 'rap',
    is_pop = lambda x: x.genres == 'pop',
    is_rnb = lambda x: x.genres == 'r&b',
    is_rock = lambda x: x.genres == 'rock',
    is_country = lambda x: x.genres == 'country'
)

In [86]:
selected_artists = artist_genres[(artist_genres.is_rap)|(artist_genres.is_pop)|(artist_genres.is_rnb)|(artist_genres.is_rock)|(artist_genres.is_country)]

In [102]:
num_genres = selected_artists.groupby('artist',as_index=False).count()

In [112]:
# Filter artists with more than 1 genre of ['pop', 'rap', 'r&b', 'country', 'roc']
selected_artists = selected_artists.merge(num_genres[num_genres.genres<=1].artist)

In [114]:
song_metadata, artist_genres = build_artist_song_dataset(selected_artists.artist.values)



  0%|          | 0/1375 [00:00<?, ?it/s]

  0%|          | 1/1375 [00:01<41:24,  1.81s/it]

Data for Yung Pinch albums and genres has been collected




  0%|          | 2/1375 [00:04<47:52,  2.09s/it]

Data for Yung Ralph albums and genres has been collected




  0%|          | 3/1375 [00:09<1:06:28,  2.91s/it]

...

Data for The Veronicas albums and genres has been collected




100%|█████████▉| 1374/1375 [1:10:47<00:03,  3.66s/it]

Data for The Verve albums and genres has been collected




100%|██████████| 1375/1375 [1:10:49<00:00,  3.09s/it]

Data for Vic Mensa albums and genres has been collected


In [115]:
song_metadata.to_csv("subsampled_genius_artist_spotify_song_metadata.csv")

### Get audio features for songs

In [8]:
song_metadata = pd.read_csv("subsampled_genius_artist_spotify_song_metadata.csv")

In [9]:
song_metadata.head()

Unnamed: 0             album artist_name                      id  \
0           0  Back 2 The Beach  Yung Pinch  3xmsmrufmGULmdWToT78jD   
1           1  Back 2 The Beach  Yung Pinch  2R3aB2ic4dLTu7VEv7DxT6   
2           2  Back 2 The Beach  Yung Pinch  0QigEd6yRtZlMnVZFoYe2b   
3           3  Back 2 The Beach  Yung Pinch  43HRfCLhkeRRNGDGoVHoW3   
4           4  Back 2 The Beach  Yung Pinch  4yHlnFIiNOze4ARV32RFPt   

                         song_name                              song_uri  \
0  Beach Ballin' (feat. blackbear)  spotify:track:3xmsmrufmGULmdWToT78jD   
1                 Lingo (feat. YG)  spotify:track:2R3aB2ic4dLTu7VEv7DxT6   
2                            Sober  spotify:track:0QigEd6yRtZlMnVZFoYe2b   
3                      Toast To Us  spotify:track:43HRfCLhkeRRNGDGoVHoW3   
4            My Friends, Not Yours  spotify:track:4yHlnFIiNOze4ARV32RFPt   

   track_number  
0           1.0  
1           2.0  
2           3.0  
3           4.0  
4           5.0

In [14]:
import random

In [18]:
sampled_song_uris = random.sample(list(song_metadata.song_uri),50000)

In [22]:
sampled_song_metadata = song_metadata.merge(pd.DataFrame({'song_uri': sampled_song_uris}))

In [27]:
sampled_song_metadata.to_csv("subsampled_song_uris.csv",index=False)

### Collect audio features for subsampled songs

In [38]:
sampled_song_metadata = pd.read_csv("subsampled_song_uris.csv")

In [50]:
finished_idx = 10910+9194

In [51]:
audio_data = audio_features(sampled_song_metadata.song_uri.values[finished_idx:])







  0%|          | 0/30494 [00:00<?, ?it/s]





  0%|          | 1/30494 [00:00<4:43:06,  1.80it/s]





  0%|          | 2/30494 [00:00<4:06:26,  2.06it/s]





  0%|          | 3/30494 [00:01<3:52:14,  2.19it/s]





  0%|          | 4/30494 [00:01<3:31:55,  2.40it/s]





  0%|          | 5/30494 [00:01<3:27:40,  2.45it/s]





  0%|          | 6/30494 [00:02<3:12:08,  2.64it/s]





  0%|          | 7/30494 [00:02<3:09:30,  2.68it/s]





  0%|          | 8/30494 [00:03<3:26:00,  2.47it/s]





  0%|          | 9/30494 [00:03<3:26:11,  2.46it/s]





  0%|          | 10/30494 [00:04<4:25:41,  1.91it/s]





  0%|          | 11/30494 [00:04<3:53:54,  2.17it/s]





  0%|          | 12/30494 [00:05<4:25:49,  1.91it/s]





  0%|          | 13/30494 [00:06<5:10:18,  1.64it/s]





  0%|          | 14/30494 [00:06<5:34:58,  1.52it/s]





  0%|          | 15/30494 [00:07<5:37:18,  1.51it/s]





  0%|          | 16/30494 [00:22<41:17:45,  4.88s/it]





  0%|          | 17/30494 [

  1%|          | 213/30494 [02:09<4:37:31,  1.82it/s]





  1%|          | 214/30494 [02:09<4:35:07,  1.83it/s]





  1%|          | 215/30494 [02:10<4:22:43,  1.92it/s]





  1%|          | 216/30494 [02:10<4:18:32,  1.95it/s]





  1%|          | 217/30494 [02:11<4:20:17,  1.94it/s]





  1%|          | 218/30494 [02:11<4:10:12,  2.02it/s]





  1%|          | 219/30494 [02:12<4:13:15,  1.99it/s]





  1%|          | 220/30494 [02:12<4:09:17,  2.02it/s]





  1%|          | 221/30494 [02:13<5:48:44,  1.45it/s]





  1%|          | 222/30494 [02:14<6:09:24,  1.37it/s]





  1%|          | 223/30494 [02:15<6:59:09,  1.20it/s]





  1%|          | 224/30494 [02:16<7:24:06,  1.14it/s]





  1%|          | 225/30494 [02:17<6:59:44,  1.20it/s]





  1%|          | 226/30494 [02:17<6:06:14,  1.38it/s]





  1%|          | 227/30494 [02:18<5:36:05,  1.50it/s]





  1%|          | 228/30494 [02:18<5:21:59,  1.57it/s]





  1%|          | 229/30494 [02:19<4:59:20,  1.69it/s]




  1%|▏         | 425/30494 [04:46<3:20:53,  2.49it/s]





  1%|▏         | 426/30494 [04:47<4:00:55,  2.08it/s]





  1%|▏         | 427/30494 [04:47<3:56:07,  2.12it/s]





  1%|▏         | 428/30494 [04:48<3:32:40,  2.36it/s]





  1%|▏         | 429/30494 [04:48<3:18:56,  2.52it/s]





  1%|▏         | 430/30494 [04:48<3:05:07,  2.71it/s]





  1%|▏         | 431/30494 [04:49<3:01:43,  2.76it/s]





  1%|▏         | 432/30494 [04:49<3:01:51,  2.76it/s]





  1%|▏         | 433/30494 [04:49<3:13:17,  2.59it/s]





  1%|▏         | 434/30494 [04:50<3:32:15,  2.36it/s]





  1%|▏         | 435/30494 [04:50<3:40:15,  2.27it/s]





  1%|▏         | 436/30494 [04:51<3:43:28,  2.24it/s]





  1%|▏         | 437/30494 [04:51<3:41:29,  2.26it/s]





  1%|▏         | 438/30494 [04:53<6:15:19,  1.33it/s]





  1%|▏         | 439/30494 [04:53<5:29:57,  1.52it/s]





  1%|▏         | 440/30494 [04:54<5:00:09,  1.67it/s]





  1%|▏         | 441/30494 [04:54<4:31:51,  1.84it/s]




  2%|▏         | 637/30494 [06:19<2:58:52,  2.78it/s]





  2%|▏         | 638/30494 [06:19<2:54:01,  2.86it/s]





  2%|▏         | 639/30494 [06:20<2:49:51,  2.93it/s]





  2%|▏         | 640/30494 [06:20<2:55:03,  2.84it/s]





  2%|▏         | 641/30494 [06:21<2:55:39,  2.83it/s]





  2%|▏         | 642/30494 [06:21<3:14:50,  2.55it/s]





  2%|▏         | 643/30494 [06:21<3:09:38,  2.62it/s]





  2%|▏         | 644/30494 [06:22<2:57:13,  2.81it/s]





  2%|▏         | 645/30494 [06:22<2:52:09,  2.89it/s]





  2%|▏         | 646/30494 [06:22<2:54:32,  2.85it/s]





  2%|▏         | 647/30494 [06:23<2:59:12,  2.78it/s]





  2%|▏         | 648/30494 [06:23<2:53:01,  2.87it/s]





  2%|▏         | 649/30494 [06:23<3:01:45,  2.74it/s]





  2%|▏         | 650/30494 [06:24<3:06:00,  2.67it/s]





  2%|▏         | 651/30494 [06:24<3:02:23,  2.73it/s]





  2%|▏         | 652/30494 [06:25<3:06:52,  2.66it/s]





  2%|▏         | 653/30494 [06:25<3:00:27,  2.76it/s]




  3%|▎         | 849/30494 [08:43<3:35:19,  2.29it/s]





  3%|▎         | 850/30494 [08:44<3:29:45,  2.36it/s]





  3%|▎         | 851/30494 [08:44<3:36:46,  2.28it/s]





  3%|▎         | 852/30494 [08:44<3:22:39,  2.44it/s]





  3%|▎         | 853/30494 [08:45<3:05:23,  2.66it/s]





  3%|▎         | 854/30494 [08:45<2:58:48,  2.76it/s]





  3%|▎         | 855/30494 [08:45<2:54:06,  2.84it/s]





  3%|▎         | 856/30494 [08:46<2:52:08,  2.87it/s]





  3%|▎         | 857/30494 [08:46<2:56:16,  2.80it/s]





  3%|▎         | 858/30494 [08:46<2:57:06,  2.79it/s]





  3%|▎         | 859/30494 [08:47<2:51:21,  2.88it/s]





  3%|▎         | 860/30494 [08:47<2:57:18,  2.79it/s]





  3%|▎         | 861/30494 [08:48<3:05:40,  2.66it/s]





  3%|▎         | 862/30494 [08:48<2:59:03,  2.76it/s]





  3%|▎         | 863/30494 [08:48<2:56:43,  2.79it/s]





  3%|▎         | 864/30494 [08:49<2:51:45,  2.88it/s]





  3%|▎         | 865/30494 [08:49<3:01:06,  2.73it/s]




...

 98%|█████████▊| 29792/30494 [3:08:50<03:23,  3.44it/s]





 98%|█████████▊| 29793/30494 [3:08:50<03:21,  3.47it/s]





 98%|█████████▊| 29794/30494 [3:08:50<03:19,  3.50it/s]





 98%|█████████▊| 29795/30494 [3:08:50<03:15,  3.58it/s]





 98%|█████████▊| 29796/30494 [3:08:51<03:22,  3.45it/s]





 98%|█████████▊| 29797/30494 [3:08:51<03:24,  3.41it/s]





 98%|█████████▊| 29798/30494 [3:08:51<03:24,  3.40it/s]





 98%|█████████▊| 29799/30494 [3:08:52<03:28,  3.33it/s]





 98%|█████████▊| 29800/30494 [3:08:52<03:35,  3.23it/s]





 98%|█████████▊| 29801/30494 [3:08:52<03:27,  3.34it/s]





 98%|█████████▊| 29802/30494 [3:08:52<03:19,  3.46it/s]





 98%|█████████▊| 29803/30494 [3:08:53<03:17,  3.49it/s]





 98%|█████████▊| 29804/30494 [3:08:53<03:16,  3.51it/s]





 98%|█████████▊| 29805/30494 [3:08:53<03:16,  3.51it/s]





 98%|█████████▊| 29806/30494 [3:08:54<03:12,  3.57it/s]





 98%|█████████▊| 29807/30494 [3:08:54<04:43,  2.42it/s]





 98%|█████████▊| 29808/3

 98%|█████████▊| 29998/30494 [3:09:51<02:25,  3.40it/s]





 98%|█████████▊| 29999/30494 [3:09:51<02:22,  3.46it/s]





 98%|█████████▊| 30000/30494 [3:09:51<02:20,  3.52it/s]





 98%|█████████▊| 30001/30494 [3:09:51<02:20,  3.52it/s]





 98%|█████████▊| 30002/30494 [3:09:52<02:20,  3.51it/s]





 98%|█████████▊| 30003/30494 [3:09:52<02:20,  3.49it/s]





 98%|█████████▊| 30004/30494 [3:09:52<02:27,  3.33it/s]





 98%|█████████▊| 30005/30494 [3:09:53<02:29,  3.28it/s]





 98%|█████████▊| 30006/30494 [3:09:53<02:31,  3.23it/s]





 98%|█████████▊| 30007/30494 [3:09:54<03:33,  2.28it/s]





 98%|█████████▊| 30008/30494 [3:09:54<03:16,  2.48it/s]





 98%|█████████▊| 30009/30494 [3:09:54<02:58,  2.72it/s]





 98%|█████████▊| 30010/30494 [3:09:55<02:45,  2.92it/s]





 98%|█████████▊| 30011/30494 [3:09:55<02:34,  3.13it/s]





 98%|█████████▊| 30012/30494 [3:09:55<02:33,  3.14it/s]





 98%|█████████▊| 30013/30494 [3:09:55<02:25,  3.31it/s]





 98%|█████████▊| 30014/3

 99%|█████████▉| 30204/30494 [3:10:54<01:23,  3.49it/s]





 99%|█████████▉| 30205/30494 [3:10:54<01:21,  3.53it/s]





 99%|█████████▉| 30206/30494 [3:10:55<01:20,  3.58it/s]





 99%|█████████▉| 30207/30494 [3:10:55<01:57,  2.44it/s]





 99%|█████████▉| 30208/30494 [3:10:56<01:46,  2.69it/s]





 99%|█████████▉| 30209/30494 [3:10:56<01:37,  2.93it/s]





 99%|█████████▉| 30210/30494 [3:10:56<01:30,  3.12it/s]





 99%|█████████▉| 30211/30494 [3:10:56<01:25,  3.30it/s]





 99%|█████████▉| 30212/30494 [3:10:57<01:21,  3.44it/s]





 99%|█████████▉| 30213/30494 [3:10:57<01:18,  3.56it/s]





 99%|█████████▉| 30214/30494 [3:10:57<01:18,  3.57it/s]





 99%|█████████▉| 30215/30494 [3:10:57<01:17,  3.59it/s]





 99%|█████████▉| 30216/30494 [3:10:58<01:16,  3.61it/s]





 99%|█████████▉| 30217/30494 [3:10:58<01:19,  3.46it/s]





 99%|█████████▉| 30218/30494 [3:10:58<01:18,  3.53it/s]





 99%|█████████▉| 30219/30494 [3:10:59<01:17,  3.56it/s]





 99%|█████████▉| 30220/3

100%|█████████▉| 30410/30494 [3:11:56<00:26,  3.18it/s]





100%|█████████▉| 30411/30494 [3:11:56<00:24,  3.35it/s]





100%|█████████▉| 30412/30494 [3:11:56<00:24,  3.32it/s]





100%|█████████▉| 30413/30494 [3:11:57<00:23,  3.42it/s]





100%|█████████▉| 30414/30494 [3:11:57<00:22,  3.53it/s]





100%|█████████▉| 30415/30494 [3:11:57<00:21,  3.60it/s]





100%|█████████▉| 30416/30494 [3:11:57<00:21,  3.60it/s]





100%|█████████▉| 30417/30494 [3:11:58<00:22,  3.49it/s]





100%|█████████▉| 30418/30494 [3:11:58<00:22,  3.40it/s]





100%|█████████▉| 30419/30494 [3:11:58<00:21,  3.48it/s]





100%|█████████▉| 30420/30494 [3:11:59<00:20,  3.53it/s]





100%|█████████▉| 30421/30494 [3:11:59<00:20,  3.58it/s]





100%|█████████▉| 30422/30494 [3:11:59<00:20,  3.56it/s]





100%|█████████▉| 30423/30494 [3:11:59<00:20,  3.53it/s]





100%|█████████▉| 30424/30494 [3:12:00<00:19,  3.58it/s]





100%|█████████▉| 30425/30494 [3:12:00<00:19,  3.58it/s]





100%|█████████▉| 30426/3

ValueError: arrays must all be same length

In [54]:
pd.read_csv("subsampled_audio_features_p3.csv")

Unnamed: 0                                   uri  danceability  energy  \
0               0  spotify:track:3QWgLzCrAVkmw5eoHPN5uB         0.412   0.965   
1               1  spotify:track:1bsQUnczB7JI4YnDzOjFMz         0.572   0.883   
2               2  spotify:track:0LPrOAd9xNlhfkkoVzzlmK         0.253   0.945   
3               3  spotify:track:2msKk0WhzOI93Hd1iFlnWv         0.260   0.979   
4               4  spotify:track:6k0EBmrgzvpyigEHGYtQiK         0.457   0.972   
...           ...                                   ...           ...     ...   
30395       30395  spotify:track:6VSVfSPEciNnqRDffXBPTn         0.625   0.793   
30396       30396  spotify:track:6dsUJXXP06W7EGqFktEIhK         0.519   0.867   
30397       30397  spotify:track:3njPfbu4Rx8w7MAhK3bdGN         0.755   0.937   
30398       30398  spotify:track:7nHk6elIYtZa4BO7LWEzE5         0.476   0.910   
30399       30399  spotify:track:3SQCEJdETNOMKje8gZBXem         0.406   0.919   

       accousticness  instrumentalness  liveness  loudness  speechiness  \
0           0.000276          0.000002    0.4080    -4.206       0.0654   
1           0.000893          0.000000    0.1020    -3.740       0.0392   
2           0.000032          0.001920    0.0709    -4.254       0.3140   
3           0.000025          0.002170    0.2780    -4.535       0.2690   
4           0.000313          0.000157    0.3370    -3.241       0.0568   
...              ...               ...       ...       ...          ...   
30395       0.012600          0.000469    0.3010    -3.696       0.0252   
30396       0.033700          0.000152    0.1290    -4.075       0.0449   
30397       0.042500          0.121000    0.0561    -3.040       0.0719   
30398       0.000096          0.000145    0.1380    -3.576       0.0663   
30399       0.004140          0.000003    0.1060    -3.647       0.0542   

         tempo  valence  popularity  
0      167.049   0.6120          51  
1      117.915   0.4690          50  
2      172.044   0.3860          39  
3      178.104   0.5660          36  
4      170.929   0.7180          39  
...        ...      ...         ...  
30395  130.944   0.4200          22  
30396  151.950   0.3730          18  
30397  133.972   0.7760          43  
30398  160.905   0.5250          29  
30399  104.970   0.0614          16  

[30400 rows x 12 columns]

In [ ]:
audio_data.to_csv("audio_feature_data_p3.csv", index=False)

In [ ]:
song_metadata.to_csv("spotify_song_metadata.csv", index=False)

In [ ]:
artist_genres.to_csv("spotify_artist_genres.csv", index=False)